In [1]:
from __future__ import print_function
import json
import datetime
import logging as log
from time import sleep
from concurrent.futures import ThreadPoolExecutor

try:
    from urllib.parse import urlparse, urlencode, urlunparse
except ImportError:
    # Python 2 imports
    from urlparse import urlparse, urlunparse
    from urllib import urlencode

import requests
from abc import ABCMeta
from abc import abstractmethod
from bs4 import BeautifulSoup

__author__ = 'Tom Dickinson'


class TwitterSearch(object):

    __meta__ = ABCMeta

    def __init__(self, rate_delay, error_delay=5):
        """
        :param rate_delay: How long to pause between calls to Twitter
        :param error_delay: How long to pause when an error occurs
        """
        self.rate_delay = rate_delay
        self.error_delay = error_delay

    def search(self, query):
        self.perform_search(query)

    def perform_search(self, query):
        """
        Scrape items from twitter
        :param query:   Query to search Twitter with. Takes form of queries constructed with using Twitters
                        advanced search: https://twitter.com/search-advanced
        """
        url = self.construct_url(query)
        continue_search = True
        min_tweet = None
        response = self.execute_search(url)
        while response is not None and continue_search and response['items_html'] is not None:
            tweets = self.parse_tweets(response['items_html'])

            # If we have no tweets, then we can break the loop early
            if len(tweets) == 0:
                break

            # If we haven't set our min tweet yet, set it now
            if min_tweet is None:
                min_tweet = tweets[0]

            continue_search = self.save_tweets(tweets)

            # Our max tweet is the last tweet in the list
            max_tweet = tweets[-1]
            if min_tweet['tweet_id'] is not max_tweet['tweet_id']:
                if "min_position" in response.keys():
                    max_position = response['min_position']
                else:
                    max_position = "TWEET-%s-%s" % (max_tweet['tweet_id'], min_tweet['tweet_id'])
                url = self.construct_url(query, max_position=max_position)
                # Sleep for our rate_delay
                sleep(self.rate_delay)
                response = self.execute_search(url)

    def execute_search(self, url):
        """
        Executes a search to Twitter for the given URL
        :param url: URL to search twitter with
        :return: A JSON object with data from Twitter
        """
        try:
            # Specify a user agent to prevent Twitter from returning a profile card
            headers = {
                'user-agent': 'Mozilla/5.0 (X11; Linux x86_64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/46.0.2490.'
                              '86 Safari/537.36'
            }
            req = requests.get(url, headers=headers)
            # response = urllib2.urlopen(req)
            data = json.loads(req.text)
            return data

        # If we get a ValueError exception due to a request timing out, we sleep for our error delay, then make
        # another attempt
        except Exception as e:
            log.error(e)
            log.error("Sleeping for %i" % self.error_delay)
            sleep(self.error_delay)
            return self.execute_search(url)

    @staticmethod
    def parse_tweets(items_html):
        """
        Parses Tweets from the given HTML
        :param items_html: The HTML block with tweets
        :return: A JSON list of tweets
        """
        soup = BeautifulSoup(items_html, "html.parser")
        tweets = []
        for li in soup.find_all("li", class_='js-stream-item'):

            # If our li doesn't have a tweet-id, we skip it as it's not going to be a tweet.
            if 'data-item-id' not in li.attrs:
                continue

            tweet = {
                'tweet_id': li['data-item-id'],
                'text': None,
                'user_id': None,
                'user_screen_name': None,
                'user_name': None,
                'created_at': None,
                'retweets': 0,
                'favorites': 0
            }

            # Tweet Text
            text_p = li.find("p", class_="tweet-text")
            if text_p is not None:
                tweet['text'] = text_p.get_text()

            # Tweet User ID, User Screen Name, User Name
            user_details_div = li.find("div", class_="tweet")
            if user_details_div is not None:
                tweet['user_id'] = user_details_div['data-user-id']
                tweet['user_screen_name'] = user_details_div['data-user-id']
                tweet['user_name'] = user_details_div['data-name']

            # Tweet date
            date_span = li.find("span", class_="_timestamp")
            if date_span is not None:
                tweet['created_at'] = float(date_span['data-time-ms'])

            # Tweet Retweets
            retweet_span = li.select("span.ProfileTweet-action--retweet > span.ProfileTweet-actionCount")
            if retweet_span is not None and len(retweet_span) > 0:
                tweet['retweets'] = int(retweet_span[0]['data-tweet-stat-count'])

            # Tweet Favourites
            favorite_span = li.select("span.ProfileTweet-action--favorite > span.ProfileTweet-actionCount")
            if favorite_span is not None and len(retweet_span) > 0:
                tweet['favorites'] = int(favorite_span[0]['data-tweet-stat-count'])

            tweets.append(tweet)
        return tweets

    @staticmethod
    def construct_url(query, max_position=None):
        """
        For a given query, will construct a URL to search Twitter with
        :param query: The query term used to search twitter
        :param max_position: The max_position value to select the next pagination of tweets
        :return: A string URL
        """

        params = {
            # Type Param
            'f': 'tweets',
            # Query Param
            'q': query
        }

        # If our max_position param is not None, we add it to the parameters
        if max_position is not None:
            params['max_position'] = max_position

        url_tupple = ('https', 'twitter.com', '/i/search/timeline', '', urlencode(params), '')
        return urlunparse(url_tupple)

    @abstractmethod
    def save_tweets(self, tweets):
        """
        An abstract method that's called with a list of tweets.
        When implementing this class, you can do whatever you want with these tweets.
        """


class TwitterSearchImpl(TwitterSearch):

    def __init__(self, rate_delay, error_delay, max_tweets):
        """
        :param rate_delay: How long to pause between calls to Twitter
        :param error_delay: How long to pause when an error occurs
        :param max_tweets: Maximum number of tweets to collect for this example
        """
        super(TwitterSearchImpl, self).__init__(rate_delay, error_delay)
        self.max_tweets = max_tweets
        self.counter = 0

    def save_tweets(self, tweets):
        """
        Just prints out tweets
        :return:
        """
        for tweet in tweets:
            # Lets add a counter so we only collect a max number of tweets
            self.counter += 1

            if tweet['created_at'] is not None:
                t = datetime.datetime.fromtimestamp((tweet['created_at']/1000))
                fmt = "%Y-%m-%d %H:%M:%S"
                log.info("%i [%s] - %s" % (self.counter, t.strftime(fmt), tweet['text']))

            # When we've reached our max limit, return False so collection stops
            if self.max_tweets is not None and self.counter >= self.max_tweets:
                return False

        return True


class TwitterSlicer(TwitterSearch):
    """
    Inspired by: https://github.com/simonlindgren/TwitterScraper/blob/master/TwitterSucker.py
    The concept is to have an implementation that actually splits the query into multiple days.
    The only additional parameters a user has to input, is a minimum date, and a maximum date.
    This method also supports parallel scraping.
    """
    def __init__(self, rate_delay, error_delay, since, until, n_threads=1):
        super(TwitterSlicer, self).__init__(rate_delay, error_delay)
        self.since = since
        self.until = until
        self.n_threads = n_threads
        self.counter = 0

    def search(self, query):
        n_days = (self.until - self.since).days
        tp = ThreadPoolExecutor(max_workers=self.n_threads)
        for i in range(0, n_days):
            since_query = self.since + datetime.timedelta(days=i)
            until_query = self.since + datetime.timedelta(days=(i + 1))
            day_query = "%s since:%s until:%s" % (query, since_query.strftime("%Y-%m-%d"),
                                                  until_query.strftime("%Y-%m-%d"))
            tp.submit(self.perform_search, day_query)
        tp.shutdown(wait=True)

    def save_tweets(self, tweets):
        """
        Just prints out tweets
        :return: True always
        """
        for tweet in tweets:
            # Lets add a counter so we only collect a max number of tweets
            self.counter += 1
            if tweet['created_at'] is not None:
                t = datetime.datetime.fromtimestamp((tweet['created_at']/1000))
                fmt = "%Y-%m-%d %H:%M:%S"
                log.info("%i [%s] - %s" % (self.counter, t.strftime(fmt), tweet['text']))

        return True


if __name__ == '__main__':
    log.basicConfig(level=log.INFO)

    search_query = "Babylon 5"
    rate_delay_seconds = 0
    error_delay_seconds = 5

    # Example of using TwitterSearch
    twit = TwitterSearchImpl(rate_delay_seconds, error_delay_seconds, None)
    twit.search(search_query)

    # Example of using TwitterSlice
    select_tweets_since = datetime.datetime.strptime("2016-10-01", '%Y-%m-%d')
    select_tweets_until = datetime.datetime.strptime("2016-12-01", '%Y-%m-%d')
    threads = 10

    twitSlice = TwitterSlicer(rate_delay_seconds, error_delay_seconds, select_tweets_since, select_tweets_until,
                              threads)
    twitSlice.search(search_query)

    print("TwitterSearch collected %i" % twit.counter)
    print("TwitterSlicer collected %i" % twitSlice.counter)

INFO:root:1 [2018-05-24 00:07:03] - These are Babylon 5 and Star Trek DS9 - 90s sci-fi I love dearly, but have episodes like “an archaeologist found this ANCIENT ARTIFACT on a MYSTERIOUS PLANET that wreaks havoc for an episode!” And they’re fun but like... real archaeology can be so interesting if you let it!
INFO:root:2 [2018-05-23 23:47:02] - .@AlyssaRosenberg what are the chances your next Act Four will mention #AmazonPrimeVideo streaming #Babylon5 starting 6/1/18.  There is so much good stuff in B5 & there is a whole audience that doesn't know of the show. It pays to let Season 1 set up future seasons. Stay with it.
INFO:root:3 [2018-05-23 23:44:47] - I liked a @YouTube video http://youtu.be/qbRrcEnJlzA?a  Babylon 5 Ruminations: S2E14 There All Honor Lies
INFO:root:4 [2018-05-23 23:35:08] - Check out what I found on eBay >> #3750 #discount #movies BABYLON  5 - CompleteSeries with Movie Col... http://rover.ebay.com/rover/1/711-53200-19255-0/1?ff3=2&toolid=10039&campid=5338246737&ite

INFO:root:44 [2018-05-23 14:46:40] - I used to have a standard offer to my internet friends: if you're ever flying through ORD, let me know and I'll meet you at the airport and treat you to a meal at one of the restaurants there.  Since 9/11, more security has made that impractical for all but the longest layovers.
INFO:root:45 [2018-05-23 13:32:10] - Wenn Du beim nächsten Artikel noch #superschwellig Babylon 5 erwähnen könntest... *g*
INFO:root:46 [2018-05-23 12:56:06] - i looked up voltron and thought the CG looked familiar. turns out it's the same CG house that Babylon 5 used!

also this pic.twitter.com/Js24btDjHP
INFO:root:47 [2018-05-23 12:48:43] - Enormous.  Probably enormous enough to fit into the codpiece in the suit of armor @BashirFaq gave @AnnoyedOBrien in the other thread.
INFO:root:48 [2018-05-23 12:46:37] - It's also nice they've built a new, smaller bridge for the Earth ships rather than the "Babylon 5 C&C with the pit covered over" look in the present day.
INFO:root:49 

INFO:root:91 [2018-05-23 05:33:12] - TOO DAZED WITH DICKS TO BOOKMARK THE BABYLON 5 FAQ
INFO:root:92 [2018-05-23 05:13:19] - Me ha gustado un vídeo de @YouTube (http://youtu.be/9SRkjOL3tNM?a  - best ending for babylon 5).
INFO:root:93 [2018-05-23 05:10:42] - (I don't do this anymore. I wish I could go back in time and apologize)

(I still like Babylon 5, but come on, past Amanda)
INFO:root:94 [2018-05-23 05:09:39] - I've definitely done embarrassing things for boys, but on the flip side, I've also made multiple partners - and also guy friends that I later realized only put up with it because they had a crush on me - watch 8 episodes of Babylon 5 in a row with me. https://twitter.com/BrandyLJensen/status/998925100811464705 …
INFO:root:95 [2018-05-23 05:04:29] - I live in Chicago, close enough to where the annual Air and Water Show is held that, when the Blue Angels or Thunderbirds turn around to fly back past the crowds, they fly over my house.  I get 4 days of air show and rehearsals a

INFO:root:136 [2018-05-22 22:14:46] - First babylon 5 is epic and that dude is awesome. Second, That other dude my be suffering from a disorder or had traumatic issue. These people can be very dangerous. Try to avoid contact with him in and out of store.
INFO:root:137 [2018-05-22 22:10:15] - I LOVE THE ORVILLE. I AM A TREK FAN BUT ONLY TOS AND ENTERPRISE, LOATHE THE OTHERS. ACTUALLY BEST SF SHOW IS BABYLON 5.
INFO:root:138 [2018-05-22 21:55:05] - @themenguin @ThatZachWilson @JessKlein1 @IAmTehran if it had been the series finale, it would have rated in my top five, along with Babylon 5, Deep Space Nine, Cheers, and Scrubs. Which in my mind is pretty good company. #AgentofSHIELD
INFO:root:139 [2018-05-22 21:32:29] - #happyanniversary #PaulWinfield #actor #captainterrel #StarTrek #TheWrathofKhan #dathon #Darmok #thenextgeneration #theterminator #marsattack #cliffhanger #babylon5 #lalaw #murdershewrote #mannix #themanfromuncle #startrek51 @TrekMovie @TrekCore @StarTrekNetflix @startrekcbs

INFO:root:175 [2018-05-22 12:17:12] - Born on this day in 1939 – Paul Winfield, American actor  - Terminator, Star Trek II: The Wrath of Khan, Damnation Alley, Mars Attacks!, Babylon 5, Star Trek: TNG, Twilight’s Last Gleaming.
 #scifi #StarTrekpic.twitter.com/xPQQ7o291l
INFO:root:176 [2018-05-22 12:11:41] - TFW I watch a premium streaming service's space ship show reboot and despite the hundred million $$ they spent producing it, it still can't live up to Babylon 5. pic.twitter.com/3TZLTFidEJ
INFO:root:177 [2018-05-22 12:02:50] - Get the first published book set in the fictional Hypervers, inspired by media like #DragonBallZ #GameOfThrones #Babylon5 and many others to create something special and unique while familiar.

https://www.amazon.com.au/gp/aw/d/B06ZYYFHBD/ref=mp_s_a_1_sc_1?ie=UTF8&qid=1526968523&sr=8-1-spell&pi=AC_SX118_SY170_QL70&keywords=regret+hypervers …
#IARTG #indie #Amazon #amazonbooks #book #regret #actionpic.twitter.com/Uo3cE7qzBT
INFO:root:178 [2018-05-22 11:58:59] 

...

INFO:root:3160 [2016-11-23 01:27:52] - Ron Thornton created CG for #Babylon5, Hypernauts, ST-DS9, ST-VOY, as well as the new Captain Scarlett. #RIPhttps://twitter.com/GerryAndersonTV/status/801065045752999936 …
INFO:root:3161 [2016-11-23 01:27:06] - #RIP Ron Thornton, 59, Emmy-winning VFX designer on 'Babylon 5.' A pioneer in bringing power of CGI to TV. http://bit.ly/2giLKjF  @B5News
INFO:root:3162 [2016-11-23 01:25:28] - THR: Ron Thornton, Emmy-winning visual effects guru on 'Babylon 5,' dies at 59 http://thr.cm/LAdCNC  pic.twitter.com/8t8mYtHxmp
INFO:root:3163 [2016-11-23 01:25:09] - THR: Ron Thornton, Emmy-winning visual effects guru on 'Babylon 5,' dies at 59 http://thr.cm/LAdCNC  pic.twitter.com/kNmMcnfChG #followme
INFO:root:3164 [2016-11-23 01:25:02] - Ron Thornton, Emmy-winning visual effects guru on 'Babylon 5,' dies at 59 http://thr.cm/LAdCNC pic.twitter.com/vYoz1lm1xc
INFO:root:3165 [2016-11-23 01:19:45] - the world seems to be turning into a plot from Babylon 5. But withou

INFO:root:3214 [2016-11-23 06:01:52] - Arrrgh, 20!6. Ron Thornton, Emmy-Winning Visual Effects Guru on 'Babylon 5,' Dies at 59 http://www.hollywoodreporter.com/news/ron-thornton-dead-babylon-5-visual-effects-designer-was-59-949981 …
INFO:root:3207 [2016-11-29 16:52:03] - I knew I shouldn't have started reading The Babylon File by Andy Lane if I wasn't ready to rewatch the whole series. #Babylon5
INFO:root:3215 [2016-11-29 15:15:25] - Star Trek rankings:
1 Next Generation
2 Babylon 5
3 Deep Space 9
4 Original Series
5 Animated Series
6 Shitty other two
INFO:root:3216 [2016-11-29 14:18:31] - I miss Babylon 5. Such good writing on it. https://twitter.com/neilhimself/status/803323407286890497 …
INFO:root:3217 [2016-11-29 13:55:41] - "I'll play Babylon 5 in the background while I draw, I've seen them all so many times"
Spend 6 hours intently watching my Babylon 5 marathon
INFO:root:3218 [2016-11-29 12:45:06] - I liked a @YouTube video http://youtu.be/Zly_tL5mMc8?a  Babylon 5 Londo sets a tr

INFO:root:3271 [2016-11-24 18:49:56] - Only Thursday but deffo my #tweetoftheweek. #Babylon5 https://twitter.com/Grumpyrocker/status/801057502762778624 …
INFO:root:3272 [2016-11-24 18:40:10] - #RIPRonThornton Special effects designer #StarTrekDS9 #Babylon5 #DoctorWho #Blakes7 @THRhttp://www.hollywoodreporter.com/news/ron-thornton-dead-babylon-5-visual-effects-designer-was-59-949981 …
INFO:root:3273 [2016-11-24 17:40:28] - [RSPBlog] Würfelheld: [ProSieben Maxx] Anime statt Star Trek und Babylon 5 http://dlvr.it/MkhC1H pic.twitter.com/HokweTextg
INFO:root:3274 [2016-11-24 17:22:58] - 「はたらくモビルスーツ」【SDガンダム Gジェネレーション ジェネシス】 (3:06) http://nico.ms/sm30093366  #sm30093366
公式かよwwwww
INFO:root:3275 [2016-11-24 17:19:38] - Babylon 5 Kosh - And so it begins https://youtu.be/3qYbVQu7YAQ 
INFO:root:3276 [2016-11-24 17:13:15] - 19:43 "When I escaped Babylon 5, I swore I put that life behind me." https://youtu.be/HnnGOT-IBMo 
INFO:root:3277 [2016-11-24 16:49:44] - Babylon 5 j'ai vu des ptit bouts, Expa

INFO:root:3326 [2016-11-24 14:22:15] - Le seul ex. d'une chrono. quasi parfaite, c Babylon5, parce que 4 saisons étaient prévue du début par le créateur.
INFO:root:3327 [2016-11-24 13:45:22] - Ron Thornton Dead: 'Babylon 5' Visual Effects Designer Was 59 ... - Hollywood Reporter: http://news.google.com/news/url?sa=t&fd=R&ct2=au&usg=AFQjCNFvBIP1oylMH35fLOJ4xl5YE1lC1g&clid=c3a7d30bb8a4878e06b80cf16b898331&cid=52779280215805&ei=bJg2WPDjGIbEuQLo3qHQAw&url=http://www.hollywoodreporter.com/news/ron-thornton-dead-babylon-5-visual-effects-designer-was-59-949981 …
INFO:root:3328 [2016-11-24 12:48:47] - wie war das noch mal mit dem @golf_podcast in der Babylon 5
INFO:root:3329 [2016-11-24 12:28:15] - http://ift.tt/2dNUwca  Babylon 5 The Complete Collection The Lost Tales DVD #Movies, #film, #trailers, #bluray, … http://ift.tt/2eg4MsP 
INFO:root:3330 [2016-11-24 11:40:14] - Ron Thornton, Emmy-Winning Visual Effects Designer of ‘Babylon 5,’ Dies at 59 http://variety.com/2016/tv/obituaries-people-n

TwitterSearch collected 19843
TwitterSlicer collected 3373


In [2]:
help(TwitterSlicer)

Help on class TwitterSlicer in module __main__:

class TwitterSlicer(TwitterSearch)
 |  Inspired by: https://github.com/simonlindgren/TwitterScraper/blob/master/TwitterSucker.py
 |  The concept is to have an implementation that actually splits the query into multiple days.
 |  The only additional parameters a user has to input, is a minimum date, and a maximum date.
 |  This method also supports parallel scraping.
 |  
 |  Method resolution order:
 |      TwitterSlicer
 |      TwitterSearch
 |      builtins.object
 |  
 |  Methods defined here:
 |  
 |  __init__(self, rate_delay, error_delay, since, until, n_threads=1)
 |      :param rate_delay: How long to pause between calls to Twitter
 |      :param error_delay: How long to pause when an error occurs
 |  
 |  save_tweets(self, tweets)
 |      Just prints out tweets
 |      :return: True always
 |  
 |  search(self, query)
 |  
 |  ----------------------------------------------------------------------
 |  Methods inherited from Twitt